In [2]:
from utils.schedule_utils import load_data_split,table_to_str,table_to_str_sql,find_intersection_and_add_row_id,Prepare_Data_for_Operator_Sequence,format_document,batch_rerank_scores,ROLLBACK,merge_clean_and_format_df_dict,retrieve_rows_by_subtables,process_error_analysis_list
import pickle
import numpy as np
import pandas as pd
import os
import json
from FlagEmbedding import FlagReranker
from tqdm import tqdm
from typing import Dict, Any
from utils.evaluator import Evaluator
from utils.prompt_generate import build_wikitq_prompt_from_df,evaluate_predictions,filter_dataframe_from_responses,fix_sql_query,match_subtables,retrieve_rows_by_subtables,build_tab_fact_prompt_from_df
from utils.async_llm import infer_prompts

/home/aizoo/miniconda3/envs/hstar/lib/python3.9/site-packages/torch/cuda/__init__.py:63: FutureWarning: The pynvml package is deprecated. Please install nvidia-ml-py instead. If you did not install pynvml directly, please report this to the maintainers of the package that installed pynvml for you.
  import pynvml  # type: ignore[import]


In [3]:
ALL_LABELS = ['Base', 'Execute_SQL', 'RAG', 'Select_Column', 'Select_Row']
def parse_valid_route(input):
    parse = eval(input)[0]
    eval_parse = eval(parse)
    ## 如果有非法字符
    return [e for e in eval_parse if e in ALL_LABELS]

In [4]:
from vllm import LLM, SamplingParams
from transformers import AutoTokenizer
import pandas as pd
import numpy as np
from time import sleep
import argparse
from vllm.lora.request import LoRARequest
import json
from tqdm import tqdm
import os 

INFO 10-22 18:50:36 [__init__.py:216] Automatically detected platform cuda.


In [5]:
## 参数记录 for wikitq ablation training-free router
N_PARALLEL = 32 ## only for convert_df_type_parallel.py of data preprocess，一次性离线的
embedding_base_model_path = '/data/workspace/yanmy/models/bge-m3'
llm_path = '/data/workspace/yanmy/models/Qwen3-4B-Instruct-2507'
router_model_path = '/data/workspace/yanmy/HybridRAG/H-STAR/router/bge-m3-finetuned/' ## fine-tuned router model path
# llm_path = ''
check_moedl_path = '/data/workspace/yanmy/HybridRAG/H-STAR/check/output/bge-reranker-v2-m3-finetuned/' ## check model path
tmp_save_path = 'datasets/schedule_test/wikitq_4B_hyper' ## 临时存储路径
dataset_name = 'wikitq'
split = 'test'
tau = 0.82
check_tau = 0.8
ALL_LABELS = [
    'Base', 'Select_Row', 'Select_Column', 'Execute_SQL', 'RAG_20_5', 
]


In [6]:
RAG_20_5 = np.load('datasets/schedule_test/wikitq/Hybrid_Retrieve_output_update.npy',allow_pickle=True).item()
wikitq_df_processed = np.load('datasets/schedule_test/wikitq/wikitq_df_processed.npy',allow_pickle=True).item()
rewrite_query_list = np.load('datasets/schedule_test/wikitq/rewrite_query.npy',allow_pickle=True)
training_free_router = pd.read_csv('../datasets/ablation/wikitq_test_training_free_router_output_4B.csv',index_col=0)
training_free_router = [parse_valid_route(x) for x in training_free_router['predict'].tolist()]
filtered_table_column = np.load('../datasets/pipeline/filtered_tables_col_test.npy',allow_pickle=True).item()
filtered_table_row = np.load('../datasets/pipeline/filtered_tables_row_test.npy',allow_pickle=True).item()
sql_exec_df_output = np.load('../datasets/pipeline/sql_exec_df_output_test.npy',allow_pickle=True).item()
sql_executable_count = np.load('../datasets/pipeline/wikitq_test_sql_executable_count_30B.npy',allow_pickle=True)
processed_table = {} ## processed_table包括了inference LLM后所有结果的聚合,key 与 method_key 保持一致
processed_table['Base'] = wikitq_df_processed
processed_table['Select_Row'] = filtered_table_row
processed_table['Select_Column'] = filtered_table_column
processed_table['RAG'] = RAG_20_5
processed_table['RAG_20_5'] = RAG_20_5
processed_table['Execute_SQL'] = sql_exec_df_output ## SQL聚合结果！
processed_table['Execute_SQL_count'] = sql_executable_count ## SQL单个结果，用作 CrossEncoder 跨模态查询
# RAG_20_5 = np.load('../datasets/pipeline/retrieved_tables_20_5_test.npy',allow_pickle=True).item()
# RAG_10_3 = np.load('../datasets/pipeline/retrieved_tables_10_3_0.5.npy',allow_pickle=True).item()

In [7]:
dataset = load_data_split(dataset_name,split)

In [8]:
## step 3: Consturct DB
from utils.multi_db_v2 import NeuralDB, Executor
table_titles = [dataset[i]['table']['page_title'] for i in range(len(dataset))]
db = NeuralDB(tables=wikitq_df_processed, table_titles=table_titles)
executor = Executor()

Initializing NeuralDB...


Creating tables in DB: 100%|██████████| 4344/4344 [01:18<00:00, 55.26it/s]


In [9]:
def Prepare_Data_for_Operator_Sequence(index,sequence,dataset, processed_table, remove_operator = []):
    data_entry = {
    'id': dataset[index]['id'],
    'query': dataset[index]['question'], ## 没有ReWrite，暂时不做变化
    # 'table': wikitq_df_processed[index],
    'title': dataset[index]['table']['page_title'], ## 不变
    # 'SQL': sql_command['sql'] + table_to_str(sql_command['table']) ,
        }
    sequence = [s for s in sequence if s not in remove_operator]
    if sequence.__contains__('Execute_SQL'): ## 有Execute_SQL计算符
        sql_list = [sql_count for sql_count in processed_table['Execute_SQL_count'] if sql_count['id']==index]
        # sql_command = sql_list[0]
        if len(sql_list)==0:
            SQL = ''
        else:
            sql_command = sql_list[0]
            SQL = sql_command['sql'] + table_to_str(sql_command['table'])
        data_entry['SQL'] = SQL
    else:
        data_entry['SQL'] = ''
    extraction_sequence = [s for s in sequence if s!='Execute_SQL']
    # print(extraction_sequence)
    if len(extraction_sequence)==1: ## Only One Operator
        method = extraction_sequence[0]
        data_entry['table'] = processed_table[method][index]
    elif len(extraction_sequence)==2:
        table_1 = processed_table[extraction_sequence[0]][index]
        table_2 = processed_table[extraction_sequence[1]][index]
        # print(table_1.shape, table_2.shape)
        table_intersection = find_intersection_and_add_row_id(table_1,table_2)
        data_entry['table'] = table_intersection
    elif len(extraction_sequence)==3:
        table_1 = processed_table[extraction_sequence[0]][index]
        table_2 = processed_table[extraction_sequence[1]][index]
        table_3 = processed_table[extraction_sequence[2]][index]
        # print(table_1.shape, table_2.shape)
        table_intersection = find_intersection_and_add_row_id(table_1,table_2)
        table_intersection = find_intersection_and_add_row_id(table_intersection,table_3)
        data_entry['table'] = table_intersection
    elif len(extraction_sequence)==0:
        data_entry['table'] = processed_table['Base'][index]
    assert data_entry.__contains__('SQL')
    assert data_entry.__contains__('table')
    return data_entry

### First we conduct our multi threshold check method

In [10]:
with open(f'datasets/schedule_test/wikitq_api_server/inference_result.pkl', 'rb') as f:
    error_analysis_row = pickle.load(f)
ranked_result = process_error_analysis_list(error_analysis_row, truncate=True, tau=tau)
# pd.DataFrame([str(r) for r in ranked_result.values()]).value_counts()

In [11]:
## step 5
## Organize LLM query list
LLM_query_list = {}
for method in ALL_LABELS:
    LLM_query_list[method] = {}
    LLM_query_list[method]['index'] = []
    LLM_query_list[method]['query'] = []
    LLM_query_list[method]['qa'] = []
for index in range(len(dataset)):
    for method in ALL_LABELS:
        if method in ranked_result[index]:
            # method_list = ranked_result[index][method]
            # method_list.append(index)
            LLM_query_list[method]['index'].extend([index])
            if method=='Select_Column':
                prompt = build_wikitq_prompt_from_df(dataset,wikitq_df_processed[index],index,template_path='../prompts/col_select_sql.txt',processed=True)
                LLM_query_list[method]['query'].extend([prompt])
            elif method=='Select_Row':
                prompt = build_wikitq_prompt_from_df(dataset,wikitq_df_processed[index],index,template_path='../prompts/row_select_sql.txt',processed=True)
                LLM_query_list[method]['query'].extend([prompt])
            elif method == 'Execute_SQL':
                prompt = build_wikitq_prompt_from_df(dataset,wikitq_df_processed[index],index,template_path='../prompts/sql_reason_wtq.txt',processed=True)
                LLM_query_list[method]['query'].extend([prompt])
            # elif method == 'Base':
            #     prompt = build_wikitq_prompt_from_df(dataset,wikitq_df_processed[index],index,template_path='../prompts/text_reason_tabfact.txt',processed=True)
            #     LLM_query_list[method]['qa'].extend([prompt])


In [22]:
col_seq_result_0 = pd.read_csv('../datasets/pipeline/wikitq_test_col_sql_output_30B.csv',index_col=0)
row_seq_result_0 = pd.read_csv('../datasets/pipeline/wikitq_test_row_sql_output_30B.csv',index_col=0)
exec_seq_result_0 = pd.read_csv('../datasets/pipeline/wikitq_test_sql_exec_output_30B.csv',index_col=0)
col_seq_result_1 = pd.read_csv('wikitq_test_col_sql_output_4B.csv',index_col=0)
row_seq_result_1 = pd.read_csv('wikitq_test_row_sql_output_4B.csv',index_col=0)
exec_seq_result_1 = pd.read_csv('wikitq_test_sql_exec_output_4B.csv',index_col=0)

In [23]:
col_sql_list = []
row_sql_list = []
exec_sql_list = []
for index in range(len(dataset)):
    current_col_list = []
    current_row_list = []
    current_exec_list = []
    current_col_list.extend(eval(col_seq_result_0.iloc[index,-1]))
    current_col_list.extend(eval(col_seq_result_1.iloc[index,-1]))
    current_row_list.extend(eval(row_seq_result_0.iloc[index,-1]))
    current_row_list.extend(eval(row_seq_result_1.iloc[index,-1]))
    current_exec_list.extend(eval(exec_seq_result_0.iloc[index,-1]))
    current_exec_list.extend(eval(exec_seq_result_1.iloc[index,-1]))
    assert len(current_col_list)==len(current_row_list)==len(current_exec_list)
    col_sql_list.append(current_col_list)
    row_sql_list.append(current_row_list)
    exec_sql_list.append(current_exec_list)

In [27]:
LLM_query_list['Select_Column']['response'] = col_sql_list
LLM_query_list['Select_Row']['response'] = row_sql_list
LLM_query_list['Execute_SQL']['response'] = exec_sql_list

- 注意相对index和绝对Index的区别

In [30]:
processed_table = {}

In [36]:
SAMPLE_NUM = 5
## step 8: SQP parse column
processed_table[SAMPLE_NUM] = {}
filtered_tables = {}
filtered_headers = {}
col_sql_index_list = LLM_query_list['Select_Column']['index']
col_sql_response_list = LLM_query_list['Select_Column']['response']
# for ind in tqdm(range(len(wikitq_df_processed))):
for i in range(len(col_sql_index_list)):
    ind = col_sql_index_list[i]
    
    input_df = wikitq_df_processed[ind]
    response_list = col_sql_response_list[ind][:SAMPLE_NUM]
    assert isinstance(response_list,list)
    filtered_table, final_headers = filter_dataframe_from_responses(response_list, input_df, add_row_id=True)
    filtered_tables[ind] = filtered_table
    filtered_headers[ind] = final_headers

## step 8: SQP parse row

from tqdm import tqdm
sub_table_list_all = {}
filtered_tables_row = {}
row_sql_index_list = LLM_query_list['Select_Row']['index']
row_sql_response_list = LLM_query_list['Select_Row']['response']
for i in range(len(row_sql_index_list)):
    # sample_num = [0,1]
    sub_table_list = []
    for sample_index in range(SAMPLE_NUM):
        ## 相对距离
        index = row_sql_index_list[i]
        #  = row_sql_response_list[i][sample_index]
        # relevant_index = row_sql_index_list.index(index)
        original_text = row_sql_response_list[index][sample_index]
        sql = fix_sql_query(response_text=original_text,table_df=wikitq_df_processed[index],table_title=table_titles[index])
        try:
            result_1 = executor.sql_exec(sql.replace('``','`').replace("COUNT(*)", "*"), db, table_id=index)
            sub_table_list.append(pd.DataFrame(result_1['rows'],columns=result_1['header']))
        except:
            continue
    print(dataset[index]['question'],dataset[index]['answer_text'])
    # match_subtables(large_table=wikitq_df_processed[index], sub_tables=[pd.DataFrame(result_1['rows'],columns=result_1['header'])])
    # pd.DataFrame(result_1['rows'],columns=result_1['header'])
    sub_table_list_all[index] = sub_table_list
    filtered_df = retrieve_rows_by_subtables(wikitq_df_processed[index],sub_table_list)
    if len(filtered_df) == 0:
        filtered_df = wikitq_df_processed[index]
    filtered_tables_row[index] = filtered_df

## step 8: SQP parse execute
from tqdm import tqdm
sample_num = SAMPLE_NUM
sql_exec_df = {}
valid_parse = 0
warning_list = []
sql_executable_count = []
exec_sql_index_list = LLM_query_list['Execute_SQL']['index']
exec_sql_response_list = LLM_query_list['Execute_SQL']['response']
# for index in tqdm(range(len(wikitq_df_processed))):
for i in range(len(exec_sql_index_list)):
    index = exec_sql_index_list[i]
    sql_exec_df[index] = []
    for sample_ind in range(sample_num):
        
        # original_text = eval(wikitq_df_output.iloc[index,-1])[sample_ind]
        original_text = exec_sql_response_list[index][sample_ind]
        sql = fix_sql_query(response_text=original_text,table_df=wikitq_df_processed[index],table_title=table_titles[index])
        if [index,sample_ind] in warning_list:
            sql = ''
            print(index,sample_ind)
        if sql!='':
            # print(result)
            try:
                result = executor.sql_exec(sql.replace('``','`'), db, table_id=index,add_row_id = True)
                df = pd.DataFrame(result['rows'],columns=result['header'])
            except:
                df = pd.DataFrame()
        else:
            df = pd.DataFrame()
        sql_exec_df[index].append(df)
        if(len(df)>0):
            valid_parse+=1
            sql_pair = {}
            sql_pair['id'] = index
            sql_pair['sample_ind'] = sample_ind
            sql_pair['sql'] = sql
            sql_pair['table'] = df
            sql_executable_count.append(sql_pair)
sql_exec_df_output = merge_clean_and_format_df_dict(sql_exec_df)

## step 8: SQP parse aggregate
 ## processed_table包括了inference LLM后所有结果的聚合,key 与 method_key 保持一致
processed_table[SAMPLE_NUM]['Base'] = wikitq_df_processed
processed_table[SAMPLE_NUM]['Select_Row'] = filtered_tables_row
processed_table[SAMPLE_NUM]['Select_Column'] = filtered_tables
processed_table[SAMPLE_NUM]['RAG_20_5'] = RAG_20_5
processed_table[SAMPLE_NUM]['Execute_SQL'] = sql_exec_df_output ## SQL聚合结果！
processed_table[SAMPLE_NUM]['Execute_SQL_count'] = sql_executable_count ## SQL单个结果，用作 CrossEncoder 跨模态查询

Executing on table_id 4 ('w4'): SELECT * FROM w WHERE `placing` = 1;
Executing on table_id 4 ('w4'): SELECT * FROM w WHERE placing = 1;
Executing on table_id 4 ('w4'): SELECT * FROM w WHERE `placing` = 1;
Executing on table_id 4 ('w4'): Decompose:  - Part 1: Count the number of 1st place finishes (placing = 1)    Response 1: SELECT * FROM w WHERE `placing` = 1;  Retrieval:  SQL: SELECT * FROM w WHERE `placing` = 1;
Executing on table_id 4 ('w4'): Decompose:  - Part 1: Count the number of 1st place finishes    Response 1: SELECT * FROM w WHERE `placing` = 1;  Retrieval:  SQL: SELECT * FROM w WHERE `placing` = 1;
what is the number of 1st place finishes across all events? ['17']
Executing on table_id 12 ('w12'): SELECT `2004`, `2005`, `2006`, `2007`, `2008` FROM w WHERE `2004` != 'none' OR `2005` != 'none' OR `2006` != 'none' OR `2007` != 'none' OR `2008` != 'none';
Executing on table_id 12 ('w12'): SELECT SUM(CASE WHEN `2004` != 'none' THEN CAST(`2004` AS INTEGER) ELSE 0 END +;
Executin

/data/workspace/yanmy/HybridRAG/H-STAR/utils/schedule_utils.py:294: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  final_df = unique_df.fillna('')
/data/workspace/yanmy/HybridRAG/H-STAR/utils/schedule_utils.py:294: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  final_df = unique_df.fillna('')
/data/workspace/yanmy/HybridRAG/H-STAR/utils/schedule_utils.py:294: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future beha

In [38]:
np.save('processed_table_all.npy',processed_table)

In [41]:
## Step 9: generated check model data 
# 对每一条数据，维护一个 Sequence_Operator
# 每条数据应该对应一个 Dict,这个Dict 包含了3 个参数：
    # id: index
    # Sequence: Operator Sequence
    # Terminated: True/False
    # Check Score: CrossEncoder 分数
    # Check Status: True/False,当前是否被计算
# 对每条数据，如果 Terminated = True，则不参与计算
# 对应的，如果 Terminated = False，那么查看 Check Status,如果 Statue=False，那么计算 Check_Score
# 每一轮计算之后，Check_Score 更新，Check Statue更新，该轮开始判定，用一个 threshold
# 如果 Check Status = True, Check Score >= Threshold，那么标注 Terminated = True，当前路径被接收
# 如果 Check Status = True, Check Score < Threshold，那么Terminated = False, Check Status = False, Check Score 清空
# Check Score 触发 RollBack 机制，即除了‘Execute_SQL'外，Extract 回退，重新计算当前流程
# 如果当前操作符只有'Execute_SQL’和空（所有 RollBack 均未被接收），那么触发 FORWARD,Terminated  = True，强制修改 Operator Sequence 为['Execute_SQL']
reranker_model = FlagReranker(check_moedl_path, use_fp16=True)
prompt_list_dict = {}
for SAMPLE_NUM in [1,2,3,4,5]:
    Check_Model_Data_Sequence = {}
    for key in ranked_result.keys(): ## 遍历所有数据,初始化
        start_sequence = ranked_result[key]
        Check_Model_Data_Sequence[key] = {}
        Check_Model_Data_Sequence[key]['id'] = key
        Check_Model_Data_Sequence[key]['Sequence'] = start_sequence
        if start_sequence == ['Base'] or start_sequence == ['Execute_SQL']: ## Terminated 不参与计算
            Check_Model_Data_Sequence[key]['Terminated'] = True
            Check_Model_Data_Sequence[key]['Check_Status'] = False
            Check_Model_Data_Sequence[key]['Check_Score'] = 0.0
        else:
            Check_Model_Data_Sequence[key]['Terminated'] = False
            Check_Model_Data_Sequence[key]['Check_Status'] = False
            Check_Model_Data_Sequence[key]['Check_Score'] = 0.0
    # Check_Model_Data_Sequence[4]
    for key in Check_Model_Data_Sequence.keys():
        data_entry = Prepare_Data_for_Operator_Sequence(key,Check_Model_Data_Sequence[key]['Sequence'],dataset, processed_table[SAMPLE_NUM])
        # data_entry = Prepare_Data_for_Operator_Sequence(key,Check_Model_Data_Sequence[key]['Sequence'],dataset, processed_table, remove_operator=['Select_Column','Select_Row'])
        # data_entry = Prepare_Data_for_Operator_Sequence(key,Check_Model_Data_Sequence[key]['Sequence'],dataset, processed_table, remove_operator=['Execute_SQL'])
        Check_Model_Data_Sequence[key]['data_entry'] = data_entry
    
    ## step 9: iterative check
    check_tau = check_tau
    count_check = 0 
    for loop in range(3):
        updated_data = batch_rerank_scores(reranker_model, Check_Model_Data_Sequence, batch_size=16)
        Check_Model_Data_Sequence = updated_data
        ## Check Terminal Status
        for key in Check_Model_Data_Sequence.keys():
            if Check_Model_Data_Sequence[key]['Terminated'] == True:
                continue
            else:
                if Check_Model_Data_Sequence[key]['Check_Status'] == True:
                    if Check_Model_Data_Sequence[key]['Check_Score'] >= check_tau: ## 0.5 threshold
                        Check_Model_Data_Sequence[key]['Terminated'] = True
                    else:
                        Check_Model_Data_Sequence[key]['Terminated'] = False
                        Check_Model_Data_Sequence[key]['Check_Status'] = False
                        Check_Model_Data_Sequence[key]['Check_Score'] = 0.0
                        current_sequence = Check_Model_Data_Sequence[key]['Sequence']
                        ROLLBACK_seq, terminated_flag = ROLLBACK(current_sequence)
                        count_check += 1
                        Check_Model_Data_Sequence[key]['Sequence'] = ROLLBACK_seq
                        Check_Model_Data_Sequence[key]['Terminated'] = terminated_flag
                        if terminated_flag == False:
                            data_entry = Prepare_Data_for_Operator_Sequence(key,ROLLBACK_seq,dataset, processed_table[SAMPLE_NUM])
                            Check_Model_Data_Sequence[key]['data_entry'] = data_entry
                else:
                    raise ValueError("Check Status should be True when Terminated is False after reranking.")

    prompt_list = []
    for index in range(len(dataset)):
        sequence = Check_Model_Data_Sequence[index]['Sequence']
        prompt = build_wikitq_prompt_from_df(dataset,Check_Model_Data_Sequence[index]['data_entry']['table'],index,template_path='../prompts/text_reason_wtq.txt',processed=True)
        if sequence==[] or sequence.__contains__('Execute_SQL'):
            try:  
                evidence = table_to_str_sql(processed_table[SAMPLE_NUM]['Execute_SQL'][index])
                prompt = prompt + evidence
            except:
                evidence = ''
                prompt = prompt + evidence
                print(f'Error for index: {index}')
        prompt_list.append(prompt)
    prompt_list_dict[SAMPLE_NUM] = prompt_list

Filtering items to rerank (Terminated=False and data_entry exists)...
Computing scores for 862 items with batch size 16...


initial target device:   0%|          | 0/2 [00:00<?, ?it/s]/home/aizoo/miniconda3/envs/hstar/lib/python3.9/site-packages/torch/cuda/__init__.py:63: FutureWarning: The pynvml package is deprecated. Please install nvidia-ml-py instead. If you did not install pynvml directly, please report this to the maintainers of the package that installed pynvml for you.
  import pynvml  # type: ignore[import]
initial target device:  50%|█████     | 1/2 [00:03<00:03,  3.82s/it]/home/aizoo/miniconda3/envs/hstar/lib/python3.9/site-packages/torch/cuda/__init__.py:63: FutureWarning: The pynvml package is deprecated. Please install nvidia-ml-py instead. If you did not install pynvml directly, please report this to the maintainers of the package that installed pynvml for you.
  import pynvml  # type: ignore[import]
Chunks: 100%|██████████| 2/2 [00:02<00:00,  1.36s/it]


Updating scores in the original dictionary...
Reranking complete.
Filtering items to rerank (Terminated=False and data_entry exists)...
Computing scores for 139 items with batch size 16...


Chunks: 100%|██████████| 2/2 [00:00<00:00,  9.53it/s]


Updating scores in the original dictionary...
Reranking complete.
Filtering items to rerank (Terminated=False and data_entry exists)...
No items to process.
Error for index: 2018
Error for index: 2359
Error for index: 2700
Filtering items to rerank (Terminated=False and data_entry exists)...
Computing scores for 862 items with batch size 16...


...

Updating scores in the original dictionary...
Reranking complete.
Filtering items to rerank (Terminated=False and data_entry exists)...
No items to process.
Error for index: 2018
Error for index: 2359
Error for index: 2552
Error for index: 2700
Filtering items to rerank (Terminated=False and data_entry exists)...
Computing scores for 862 items with batch size 16...


Chunks: 100%|██████████| 2/2 [00:01<00:00,  1.72it/s]


Updating scores in the original dictionary...
Reranking complete.
Filtering items to rerank (Terminated=False and data_entry exists)...
Computing scores for 115 items with batch size 16...


Chunks: 100%|██████████| 2/2 [00:00<00:00,  7.17it/s]


Updating scores in the original dictionary...
Reranking complete.
Filtering items to rerank (Terminated=False and data_entry exists)...
No items to process.
Error for index: 2018
Error for index: 2359
Error for index: 2552
Error for index: 2700


In [42]:
np.save('prompt_list_dict',prompt_list_dict)

In [48]:
reranker_model = FlagReranker(check_moedl_path, use_fp16=True)

In [50]:
for sample_num in [1,2,3,4,5]:
    prompt_list = prompt_list_dict[sample_num]
    qa_final = infer_prompts(prompt_list,temperature=0, top_p=1, sample_num=1,llm_path=llm_path)
    wikitq_df = pd.DataFrame(dataset)
    wikitq_df['instruction'] = prompt_list
    wikitq_df['predict'] = qa_final[0]
    ## step 12: evaluate
    wikitq_df['predict'] = [str(s) for s in qa_final[0]]
    acc_all, error_index_all, format_error_index_all = evaluate_predictions(dataset_name, wikitq_df, dataset)
    print(f'SAMPLE_NUM {sample_num} Accuracy: {acc_all}')

Processed prompts: 100%|██████████| 4344/4344 [09:41<00:00,  7.46it/s, est. speed input=16002.86 toks/s, output=1999.20 toks/s]


  0%|          | 0/4344 [00:00<?, ?it/s]

Correct Samples: 3319; Total Samples: 4344
Accuracy: 76.40
SAMPLE_NUM 1 Accuracy: 76.40423572744015


Processed prompts: 100%|██████████| 4344/4344 [09:52<00:00,  7.33it/s, est. speed input=15782.70 toks/s, output=1988.92 toks/s]


  0%|          | 0/4344 [00:00<?, ?it/s]

...

  0%|          | 0/4344 [00:00<?, ?it/s]

Correct Samples: 3376; Total Samples: 4344
Accuracy: 77.72
SAMPLE_NUM 4 Accuracy: 77.71639042357275


Processed prompts: 100%|██████████| 4344/4344 [10:22<00:00,  6.98it/s, est. speed input=15210.05 toks/s, output=1923.47 toks/s] 


  0%|          | 0/4344 [00:00<?, ?it/s]

Correct Samples: 3376; Total Samples: 4344
Accuracy: 77.72
SAMPLE_NUM 5 Accuracy: 77.71639042357275


Processed prompts: 100%|██████████| 4344/4344 [09:41<00:00,  7.46it/s, est. speed input=16002.86 toks/s, output=1999.20 toks/s]
Correct Samples: 3319; Total Samples: 4344
Accuracy: 76.40
SAMPLE_NUM 1 Accuracy: 76.40423572744015
Processed prompts: 100%|██████████| 4344/4344 [09:52<00:00,  7.33it/s, est. speed input=15782.70 toks/s, output=1988.92 toks/s]
Correct Samples: 3362; Total Samples: 4344
Accuracy: 77.39
SAMPLE_NUM 2 Accuracy: 77.39410681399632
Processed prompts: 100%|██████████| 4344/4344 [10:07<00:00,  7.15it/s, est. speed input=15453.73 toks/s, output=1904.24 toks/s]
Correct Samples: 3367; Total Samples: 4344
Accuracy: 77.51
SAMPLE_NUM 3 Accuracy: 77.50920810313076
Processed prompts: 100%|██████████| 4344/4344 [10:23<00:00,  6.96it/s, est. speed input=15126.53 toks/s, output=1896.97 toks/s]
Correct Samples: 3376; Total Samples: 4344
Accuracy: 77.72
SAMPLE_NUM 4 Accuracy: 77.71639042357275
Processed prompts: 100%|██████████| 4344/4344 [10:22<00:00,  6.98it/s, est. speed input=15210.05 toks/s, output=1923.47 toks/s] 
Correct Samples: 3376; Total Samples: 4344
Accuracy: 77.72
SAMPLE_NUM 5 Accuracy: 77.71639042357275

In [ ]:
sample_num_metrics = {}
for sample_num in [1,2,3,4,5]:
    sample_num_metrics[sample_num] = {}

sample_num_metrics[1]['acc'] = 3319 / 4344
sample_num_metrics[2]['acc'] = 3362 / 4344
sample_num_metrics[3]['acc'] = 3367 / 4344
sample_num_metrics[4]['acc'] = 3376 / 4344
sample_num_metrics[5]['acc'] = 3376 / 4344

sample_num_metrics[1]['time'] = 9*60+41
sample_num_metrics[2]['time'] = 9*60+52
sample_num_metrics[3]['time'] = 10*60+7
sample_num_metrics[4]['time'] = 10*60+23
sample_num_metrics[5]['time'] = 10*60+22